# Allen Cell Types
## Exploratory Data Analysis

### Setup

In [15]:
from allensdk.core.cell_types_cache import CellTypesCache
from allensdk.api.queries.cell_types_api import CellTypesApi
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import os

In [16]:
%matplotlib inline
plt.rcParams['figure.dpi'] = 1200
plt.rcParams['savefig.dpi'] = 1200
plt.rcParams.update({'font.size': 14})

In [17]:
dir_path = os.getcwd()
mouse_data = pd.read_csv(dir_path + '/data/mouse/ephys_data.csv')
human_data = pd.read_csv(dir_path + '/data/human/ephys_data.csv')
savepath = dir_path + '/results/eda'

In [18]:
ctc = CellTypesCache()
cells = ctc.get_cells(species=[CellTypesApi.MOUSE])

### Inspect the electrophysiological response of a neuron according to a stimulus

In [19]:
def get_stimulation_and_response():
    for ind, cell in enumerate(cells):
        cell_id = cell['id']
        data_set = ctc.get_ephys_data(cell_id)
        sweeps = ctc.get_ephys_sweeps(cell_id)
        noise_sweep_number = [x['sweep_number'] for x in sweeps
                              if x['stimulus_name'] in ['Noise 1', 'Noise 2']
                              and x['num_spikes'] is not None
                              and x['num_spikes'] > 10]
        if not noise_sweep_number:
            continue

        try:
            sweep_data = data_set.get_sweep(noise_sweep_number[0])
            return sweep_data
        except:
            continue

In [20]:
def plot_stimulation_and_response(data):
    relevant_signal = range(*data['index_range'])
    stimulation = data['stimulus'][relevant_signal]  # in A
    stimulation *= 1e12  # to pA
    response = data['response'][relevant_signal]  # in V
    response *= 1e3  # to mV

    fig, axes = plt.subplots(2, 1, figsize=(8, 6))
    axes[0].plot(np.linspace(0, 9, len(relevant_signal)), stimulation, 'b-', linewidth=0.5, alpha=0.7)
    axes[0].set_xlabel('Seconds')
    axes[0].set_ylabel('pA')
    axes[0].set_title('Stimulation')

    axes[1].plot(np.linspace(0, 9, len(relevant_signal)), response, 'r-', linewidth=0.1, alpha=0.7)
    axes[1].set_xlabel('Seconds')
    axes[1].set_ylabel('mV')
    axes[1].set_ylim([-80, 50])
    axes[1].set_title('Response')

    plt.subplots_adjust(hspace=0.5)
    fig.suptitle('Electrophysiological activity of a neuron')
    plt.show()
    fig.savefig(savepath + "/stimulation_response.png", dpi=1200)

In [21]:
sweep_data = get_stimulation_and_response()
plot_stimulation_and_response(sweep_data)

### What is the distribution of excitatory and inhibitory cells in the data?

In [22]:
def plot_cell_distribution():
    fig, axes = plt.subplots(1, 2, sharey='all', figsize=(8, 6))
    fig.suptitle('Distribution of inhibitory/excitatory cells')

    axes[0].set_title('Mouse data')
    ax0 = sns.countplot(ax=axes[0], x="dendrite_type", data=mouse_data, palette="Set2",
                        order=['spiny', 'aspiny'])
    ax0.set(xlabel=None)

    axes[1].set_title('Human data')
    ax1 = sns.countplot(ax=axes[1], x="dendrite_type", data=human_data, palette="Set2",
                        order=['spiny', 'aspiny'])
    ax1.set(xlabel=None)

    plt.tight_layout()
    plt.show()
    fig.savefig(savepath + "/dendrite_type.png", dpi=1200)

In [23]:
plot_cell_distribution()

### What is the distribution of Cre-line targeting in the data?

In [24]:
def plot_types():
    fig = plt.figure(figsize=(8, 6))
    fig.suptitle('Distribution of t-types (merged)')
    ax = sns.countplot(x="transgenic_line", data=mouse_data, palette="Set2",
                       order=mouse_data['transgenic_line'].value_counts().index)
    ax.bar_label(ax.containers[0])
    ax.set(xlabel=None)
    plt.tight_layout()
    plt.show()
    fig.savefig(savepath + "/t_type.png", dpi=1200)

In [25]:
plot_types()

### What is the Cre-line distribution in each layer?

In [26]:
def plot_cre_line_in_layers():
    fig = plt.figure(figsize=(12, 10))
    fig.suptitle('Distribution of Cre-lines in each layer')
    g = sns.countplot(x="layer", data=mouse_data, hue="transgenic_line",
                      order=['L1', 'L2/L3', 'L4', 'L5', 'L6a', 'L6b'], palette="Set2")
    total = float(len(mouse_data))
    for p in g.axes.patches:
        percentage = '{:.1f}%'.format(100 * p.get_height() / total)
        x = p.get_x() + p.get_width()
        y = p.get_height()
        g.axes.annotate(percentage, (x, y), ha='right', va='baseline', rotation=50, fontsize='medium')

    plt.tight_layout()
    plt.show()
    fig.savefig(savepath + "/t_type_layer.png", dpi=1200)

In [27]:
plot_cre_line_in_layers()